# Download data

In [5]:
%%bash
apt install unzip
mkdir -p data
cd data
if [ ! -f "ml-20m.zip" ]; then
    echo "Downloading data"
    wget http://files.grouplens.org/datasets/movielens/ml-20m.zip
    unzip ml-20m.zip
fi

Reading package lists...
Building dependency tree...
Reading state information...
unzip is already the newest version (6.0-21ubuntu1).
0 upgraded, 0 newly installed, 0 to remove and 32 not upgraded.


In [6]:
!ls ./data

ml-20m	ml-20m.zip


In [7]:
from argparse import ArgumentParser
import pandas as pd
import numpy as np
import torch
from tqdm import tqdm

In [8]:
MIN_RATINGS = 20
USER_COLUMN = 'userId'
ITEM_COLUMN = 'movieId'

In [9]:
df = pd.read_csv('./data/ml-20m/ratings.csv')
print("Filtering out users with less than {} ratings".format(MIN_RATINGS))
grouped = df.groupby(USER_COLUMN)
df = grouped.filter(lambda x: len(x) >= MIN_RATINGS)

Filtering out users with less than 20 ratings


In [10]:
# Need to sort before popping to get last item
df.sort_values(by='timestamp', inplace=True)

# clean up data
del df['rating'], df['timestamp']
df = df.drop_duplicates() # assuming it keeps order

# now we have filtered and sorted by time data, we can split test data out
grouped_sorted = df.groupby(USER_COLUMN, group_keys=False)
test_data = grouped_sorted.tail(1).sort_values(by=USER_COLUMN)
# need to pop for each group
train_data = grouped_sorted.apply(lambda x: x.iloc[:-1])

In [11]:
train_data['target']=1
test_data['target']=1


In [12]:
train_data.head()

userId  movieId  target
20       1      924       1
19       1      919       1
86       1     2683       1
61       1     1584       1
23       1     1079       1

In [24]:
from collections import defaultdict 
import os
import pickle

if not os.path.exists('/workspace/dlrm_vinhn/notebooks/user_item_dicts.pickle'):
    print('building dict...')
    user_items_train = defaultdict(set)
    item_users_train = defaultdict(set)
    for _, row in tqdm(train_data.iterrows()):
        user_items_train[row['userId']].add(row['movieId'])
        item_users_train[row['movieId']].add(row['userId'])

    user_items_test = defaultdict(set)
    item_users_test = defaultdict(set)
    for _, row in tqdm(test_data.iterrows()):
        user_items_test[row['userId']].add(row['movieId'])
        item_users_test[row['movieId']].add(row['userId'])

    import pickle

    with open('./user_item_dicts.pickle', 'wb') as handle:
        pickle.dump({"user_items_train": user_items_train, 
                     "item_users_train": item_users_train,
                     "user_items_test": user_items_test,
                     "item_users_test": item_users_test,
                    }, handle, protocol=pickle.HIGHEST_PROTOCOL)
else:
    with open('/workspace/dlrm_vinhn/notebooks/user_item_dicts.pickle', 'rb') as handle:
        dat = pickle.load(handle)
        user_items_train = dat["user_items_train"]
        item_users_train = dat["item_users_train"]
        user_items_test = dat["user_items_test"]
        item_users_test = dat["item_users_test"]




0it [00:00, ?it/s]


758it [00:00, 7571.47it/s]

building dict...





1605it [00:00, 7818.49it/s]


2497it [00:00, 8118.78it/s]


3380it [00:00, 8317.37it/s]


4272it [00:00, 8487.84it/s]


5129it [00:00, 8510.69it/s]


6012it [00:00, 8602.56it/s]


6894it [00:00, 8665.77it/s]


7770it [00:00, 8691.91it/s]


8668it [00:01, 8773.86it/s]


9549it [00:01, 8784.19it/s]


10430it [00:01, 8791.18it/s]


11302it [00:01, 8767.98it/s]


12186it [00:01, 8787.08it/s]


13060it [00:01, 8761.69it/s]


13945it [00:01, 8787.63it/s]


14834it [00:01, 8815.95it/s]


15723it [00:01, 8835.91it/s]


16606it [00:01, 8800.37it/s]


17486it [00:02, 8794.07it/s]


18367it [00:02, 8797.26it/s]


19257it [00:02, 8826.06it/s]


20140it [00:02, 8819.36it/s]


21034it [00:02, 8853.60it/s]


21922it [00:02, 8859.15it/s]


22810it [00:02, 8864.81it/s]


23699it [00:02, 8870.95it/s]


24587it [00:02, 8862.64it/s]


25474it [00:02, 8863.47it/s]


26365it [00:03, 8874.65it/s]


27253it [00:03, 8849.83it/s]


28138it [00:03, 8836.56it/s]


29023it [00:03, 8840.53it/s]


29910it [00:03,

182357it [00:20, 8893.73it/s]


183255it [00:20, 8917.08it/s]


184147it [00:20, 8904.09it/s]


185044it [00:20, 8922.06it/s]


185942it [00:20, 8938.35it/s]


186837it [00:20, 8939.64it/s]


187733it [00:21, 8944.71it/s]


188633it [00:21, 8958.53it/s]


189530it [00:21, 8960.37it/s]


190427it [00:21, 8957.87it/s]


191325it [00:21, 8963.24it/s]


192222it [00:21, 8959.71it/s]


193118it [00:21, 8958.51it/s]


194017it [00:21, 8965.65it/s]


194915it [00:21, 8967.42it/s]


195812it [00:21, 8964.21it/s]


196709it [00:22, 8955.81it/s]


197609it [00:22, 8968.54it/s]


198506it [00:22, 8956.99it/s]


199402it [00:22, 8953.69it/s]


200299it [00:22, 8957.27it/s]


201195it [00:22, 8953.15it/s]


202091it [00:22, 8903.60it/s]


202982it [00:22, 8877.45it/s]


203876it [00:22, 8896.06it/s]


204772it [00:22, 8914.48it/s]


205668it [00:23, 8927.13it/s]


206568it [00:23, 8947.62it/s]


207463it [00:23, 8947.45it/s]


208362it [00:23, 8959.56it/s]


209258it [00:23, 8936.75it/s]


210152it

360414it [00:40, 8742.90it/s]


361289it [00:40, 8639.69it/s]


362154it [00:40, 8583.55it/s]


363038it [00:40, 8656.58it/s]


363929it [00:40, 8729.56it/s]


364815it [00:40, 8767.72it/s]


365702it [00:41, 8795.30it/s]


366587it [00:41, 8809.28it/s]


367478it [00:41, 8836.94it/s]


368374it [00:41, 8871.27it/s]


369264it [00:41, 8878.67it/s]


370152it [00:41, 8876.23it/s]


371045it [00:41, 8889.93it/s]


371936it [00:41, 8894.95it/s]


372826it [00:41, 8889.90it/s]


373716it [00:41, 8848.84it/s]


374602it [00:42, 8850.06it/s]


375497it [00:42, 8876.91it/s]


376386it [00:42, 8878.23it/s]


377279it [00:42, 8891.37it/s]


378169it [00:42, 8871.62it/s]


379057it [00:42, 8867.48it/s]


379944it [00:42, 8862.36it/s]


380831it [00:42, 8824.04it/s]


381714it [00:42, 8783.54it/s]


382602it [00:42, 8809.71it/s]


383490it [00:43, 8828.13it/s]


384385it [00:43, 8863.47it/s]


385272it [00:43, 8860.01it/s]


386165it [00:43, 8879.77it/s]


387054it [00:43, 8838.26it/s]


387940it

...

19276655it [36:09, 8782.72it/s]


19277536it [36:09, 8790.13it/s]


19278418it [36:09, 8797.98it/s]


19279302it [36:09, 8809.34it/s]


19280183it [36:09, 8803.80it/s]


19281064it [36:09, 8805.41it/s]


19281948it [36:09, 8813.59it/s]


19282830it [36:10, 8803.02it/s]


19283711it [36:10, 8781.35it/s]


19284592it [36:10, 8787.06it/s]


19285478it [36:10, 8806.05it/s]


19286363it [36:10, 8816.83it/s]


19287247it [36:10, 8821.72it/s]


19288133it [36:10, 8832.69it/s]


19289017it [36:10, 8815.75it/s]


19289899it [36:10, 8809.06it/s]


19290780it [36:10, 8728.59it/s]


19291659it [36:11, 8745.04it/s]


19292537it [36:11, 8753.22it/s]


19293417it [36:11, 8766.24it/s]


19294302it [36:11, 8790.07it/s]


19295182it [36:11, 8789.47it/s]


19296065it [36:11, 8799.37it/s]


19296945it [36:11, 8789.00it/s]


19297825it [36:11, 8790.00it/s]


19298707it [36:11, 8797.80it/s]


19299592it [36:11, 8812.09it/s]


19300477it [36:12, 8822.76it/s]


19301360it [36:12, 8823.31it/s]


19302243it [36

19443899it [36:28, 8788.62it/s]


19444779it [36:28, 8783.94it/s]


19445663it [36:28, 8800.61it/s]


19446561it [36:28, 8851.19it/s]


19447455it [36:28, 8874.93it/s]


19448349it [36:28, 8894.17it/s]


19449239it [36:29, 8887.09it/s]


19450128it [36:29, 8876.07it/s]


19451016it [36:29, 8856.48it/s]


19451902it [36:29, 8847.62it/s]


19452790it [36:29, 8855.93it/s]


19453683it [36:29, 8875.18it/s]


19454571it [36:29, 8831.72it/s]


19455461it [36:29, 8851.77it/s]


19456347it [36:29, 8736.10it/s]


19457221it [36:29, 8643.06it/s]


19458086it [36:30, 8573.25it/s]


19458958it [36:30, 8616.63it/s]


19459851it [36:30, 8705.97it/s]


19460723it [36:30, 8686.51it/s]


19461613it [36:30, 8748.68it/s]


19462495it [36:30, 8767.76it/s]


19463381it [36:30, 8793.60it/s]


19464261it [36:30, 8722.47it/s]


19465138it [36:30, 8736.21it/s]


19466014it [36:30, 8741.91it/s]


19466904it [36:31, 8786.88it/s]


19467785it [36:31, 8793.46it/s]


19468677it [36:31, 8829.41it/s]


19469569it [36

19612377it [36:47, 8885.36it/s]


19613268it [36:47, 8890.84it/s]


19614158it [36:47, 8865.95it/s]


19615045it [36:47, 8833.48it/s]


19615932it [36:47, 8842.35it/s]


19616817it [36:48, 8821.47it/s]


19617700it [36:48, 8805.87it/s]


19618588it [36:48, 8825.80it/s]


19619475it [36:48, 8837.67it/s]


19620366it [36:48, 8858.65it/s]


19621256it [36:48, 8868.14it/s]


19622143it [36:48, 8845.77it/s]


19623032it [36:48, 8857.15it/s]


19623925it [36:48, 8876.06it/s]


19624813it [36:48, 8842.38it/s]


19625708it [36:49, 8873.12it/s]


19626596it [36:49, 8861.38it/s]


19627487it [36:49, 8875.66it/s]


19628375it [36:49, 8757.30it/s]


19629252it [36:49, 8712.19it/s]


19630124it [36:49, 7441.50it/s]


19630986it [36:49, 7759.03it/s]


19631867it [36:49, 8047.01it/s]


19632735it [36:49, 8226.53it/s]


19633624it [36:50, 8414.18it/s]


19634506it [36:50, 8531.67it/s]


19635376it [36:50, 8581.14it/s]


19636262it [36:50, 8660.50it/s]


19637150it [36:50, 8724.77it/s]


19638037it [36

19783818it [37:06, 9080.91it/s]


19784727it [37:06, 9064.47it/s]


19785640it [37:06, 9083.30it/s]


19786551it [37:06, 9088.44it/s]


19787467it [37:07, 9107.75it/s]


19788378it [37:07, 9107.66it/s]


19789289it [37:07, 9091.37it/s]


19790199it [37:07, 9091.65it/s]


19791109it [37:07, 9046.42it/s]


19792014it [37:07, 9043.77it/s]


19792930it [37:07, 9076.41it/s]


19793838it [37:07, 9074.43it/s]


19794754it [37:07, 9099.31it/s]


19795668it [37:07, 9109.97it/s]


19796580it [37:08, 9112.96it/s]


19797492it [37:08, 9077.46it/s]


19798403it [37:08, 9086.73it/s]


19799312it [37:08, 9086.51it/s]


19800221it [37:08, 9060.20it/s]


19801128it [37:08, 9051.78it/s]


19802034it [37:08, 9044.39it/s]


19802939it [37:08, 9045.57it/s]


19803852it [37:08, 9069.53it/s]


19804761it [37:08, 9073.73it/s]


19805669it [37:09, 9042.86it/s]


19806583it [37:09, 9070.08it/s]


19807496it [37:09, 9087.95it/s]


19808410it [37:09, 9101.04it/s]


19809321it [37:09, 9102.22it/s]


19810232it [37

98221it [00:14, 8977.64it/s]


99119it [00:14, 8964.46it/s]


100022it [00:14, 8983.43it/s]


100924it [00:14, 8993.82it/s]


101824it [00:14, 8973.84it/s]


102722it [00:14, 8952.39it/s]


103621it [00:14, 8963.57it/s]


104518it [00:14, 8938.89it/s]


105412it [00:14, 8871.54it/s]


106312it [00:14, 8907.53it/s]


107206it [00:15, 8914.88it/s]


108107it [00:15, 8941.93it/s]


109007it [00:15, 8958.60it/s]


109911it [00:15, 8980.16it/s]


110810it [00:15, 8973.02it/s]


111708it [00:15, 8934.95it/s]


112602it [00:15, 8905.97it/s]


113502it [00:15, 8931.49it/s]


114404it [00:15, 8956.67it/s]


115300it [00:15, 8877.35it/s]


116188it [00:18, 1060.97it/s]


117082it [00:18, 1442.27it/s]


117965it [00:18, 1925.59it/s]


118799it [00:18, 2503.06it/s]


119689it [00:18, 3190.86it/s]


120581it [00:19, 3952.05it/s]


121468it [00:19, 4739.93it/s]


122363it [00:19, 5518.59it/s]


123264it [00:19, 6243.29it/s]


124154it [00:19, 6856.41it/s]


125044it [00:19, 7361.70it/s]


125942it [

In [25]:
users = list(np.unique(df['userId']))
items = list(np.unique(df['movieId']))

In [26]:
def NegativeSampling(user_items, items, neg_sample_factor=5):
    neg_user_items = defaultdict(set)
    cnt = 0
    for user in tqdm(user_items):
        num_rating = len(user_items[user])
        num_neg = neg_sample_factor * num_rating
        
        idx = np.random.randint(0, len(items), (int(num_neg*1.2)))
        
        for i in idx:
            if items[i] not in user_items[user]:
                neg_user_items[user].add(items[i])
            if len(neg_user_items[user]) == num_neg:
                break
        
        cnt += len(neg_user_items[user])
    return neg_user_items, cnt

In [27]:
train_negs, num_train_negs = NegativeSampling(user_items_train, items, 30)




  0%|          | 0/138493 [00:00<?, ?it/s]


  0%|          | 58/138493 [00:00<04:14, 544.93it/s]


  0%|          | 116/138493 [00:00<04:19, 533.43it/s]


  0%|          | 156/138493 [00:00<05:09, 447.63it/s]


  0%|          | 220/138493 [00:00<04:42, 490.33it/s]


  0%|          | 271/138493 [00:00<04:44, 486.38it/s]


  0%|          | 313/138493 [00:00<05:05, 452.79it/s]


  0%|          | 359/138493 [00:00<05:17, 434.82it/s]


  0%|          | 400/138493 [00:00<05:54, 389.16it/s]


  0%|          | 438/138493 [00:01<06:19, 364.12it/s]


  0%|          | 474/138493 [00:01<06:25, 358.31it/s]


  0%|          | 521/138493 [00:01<05:58, 384.60it/s]


  0%|          | 560/138493 [00:01<06:10, 372.64it/s]


  0%|          | 598/138493 [00:01<06:26, 356.47it/s]


  0%|          | 635/138493 [00:01<06:42, 342.85it/s]


  0%|          | 676/138493 [00:01<06:22, 360.18it/s]


  1%|          | 717/138493 [00:01<06:12, 370.19it/s]


  1%|          | 755/138493 [00:01<06:41, 343.32it/s]


 

  4%|▍         | 5303/138493 [00:14<05:39, 392.04it/s]


  4%|▍         | 5343/138493 [00:14<05:41, 389.70it/s]


  4%|▍         | 5383/138493 [00:14<07:13, 307.36it/s]


  4%|▍         | 5418/138493 [00:14<07:00, 316.11it/s]


  4%|▍         | 5465/138493 [00:14<06:24, 346.35it/s]


  4%|▍         | 5503/138493 [00:14<06:29, 341.53it/s]


  4%|▍         | 5539/138493 [00:15<06:53, 321.85it/s]


  4%|▍         | 5580/138493 [00:15<06:27, 343.40it/s]


  4%|▍         | 5623/138493 [00:15<06:15, 353.73it/s]


  4%|▍         | 5691/138493 [00:15<05:22, 411.28it/s]


  4%|▍         | 5737/138493 [00:15<05:51, 377.55it/s]


  4%|▍         | 5779/138493 [00:15<05:46, 382.83it/s]


  4%|▍         | 5820/138493 [00:15<05:56, 371.65it/s]


  4%|▍         | 5859/138493 [00:15<06:23, 346.08it/s]


  4%|▍         | 5908/138493 [00:15<05:53, 375.05it/s]


  4%|▍         | 5954/138493 [00:16<05:36, 393.91it/s]


  4%|▍         | 6002/138493 [00:16<05:18, 416.30it/s]


  4%|▍         | 6046/138493 [0

  8%|▊         | 10695/138493 [00:29<10:18, 206.65it/s]


  8%|▊         | 10725/138493 [00:29<09:20, 227.89it/s]


  8%|▊         | 10759/138493 [00:29<09:04, 234.63it/s]


  8%|▊         | 10784/138493 [00:29<10:28, 203.15it/s]


  8%|▊         | 10807/138493 [00:30<10:10, 209.14it/s]


  8%|▊         | 10830/138493 [00:30<10:18, 206.29it/s]


  8%|▊         | 10866/138493 [00:30<09:01, 235.59it/s]


  8%|▊         | 10895/138493 [00:30<09:38, 220.60it/s]


  8%|▊         | 10919/138493 [00:30<09:49, 216.24it/s]


  8%|▊         | 10942/138493 [00:30<10:30, 202.38it/s]


  8%|▊         | 10976/138493 [00:30<09:14, 230.02it/s]


  8%|▊         | 11002/138493 [00:30<09:25, 225.60it/s]


  8%|▊         | 11035/138493 [00:31<08:33, 248.32it/s]


  8%|▊         | 11074/138493 [00:31<07:43, 274.84it/s]


  8%|▊         | 11104/138493 [00:31<08:50, 240.14it/s]


  8%|▊         | 11132/138493 [00:31<08:28, 250.33it/s]


  8%|▊         | 11165/138493 [00:31<07:52, 269.37it/s]


  8%|▊        

 11%|█▏        | 15718/138493 [00:44<07:22, 277.75it/s]


 11%|█▏        | 15750/138493 [00:44<07:47, 262.41it/s]


 11%|█▏        | 15789/138493 [00:44<07:04, 288.82it/s]


 11%|█▏        | 15825/138493 [00:45<06:43, 303.88it/s]


 11%|█▏        | 15871/138493 [00:45<06:03, 337.59it/s]


 11%|█▏        | 15908/138493 [00:45<06:02, 338.49it/s]


 12%|█▏        | 15944/138493 [00:45<06:22, 320.31it/s]


 12%|█▏        | 15993/138493 [00:45<05:46, 353.86it/s]


 12%|█▏        | 16041/138493 [00:45<05:21, 381.43it/s]


 12%|█▏        | 16082/138493 [00:45<05:34, 365.50it/s]


 12%|█▏        | 16122/138493 [00:45<05:27, 373.29it/s]


 12%|█▏        | 16161/138493 [00:45<05:59, 340.35it/s]


 12%|█▏        | 16197/138493 [00:46<06:19, 322.10it/s]


 12%|█▏        | 16235/138493 [00:46<06:03, 336.30it/s]


 12%|█▏        | 16270/138493 [00:46<06:20, 320.99it/s]


 12%|█▏        | 16320/138493 [00:46<05:39, 359.59it/s]


 12%|█▏        | 16359/138493 [00:46<05:39, 359.38it/s]


 12%|█▏       

 15%|█▌        | 21115/138493 [00:59<04:57, 394.70it/s]


 15%|█▌        | 21157/138493 [00:59<04:56, 396.01it/s]


 15%|█▌        | 21198/138493 [00:59<05:51, 333.84it/s]


 15%|█▌        | 21257/138493 [00:59<05:05, 383.65it/s]


 15%|█▌        | 21300/138493 [00:59<05:34, 350.34it/s]


 15%|█▌        | 21340/138493 [00:59<05:23, 362.64it/s]


 15%|█▌        | 21379/138493 [00:59<05:26, 358.54it/s]


 15%|█▌        | 21417/138493 [00:59<06:14, 312.62it/s]


 16%|█▌        | 21486/138493 [01:00<05:13, 373.16it/s]


 16%|█▌        | 21537/138493 [01:00<04:49, 404.54it/s]


 16%|█▌        | 21592/138493 [01:00<04:26, 437.99it/s]


 16%|█▌        | 21641/138493 [01:00<04:26, 437.96it/s]


 16%|█▌        | 21689/138493 [01:00<04:43, 412.34it/s]


 16%|█▌        | 21733/138493 [01:00<04:46, 408.16it/s]


 16%|█▌        | 21789/138493 [01:00<04:24, 441.71it/s]


 16%|█▌        | 21836/138493 [01:00<04:23, 443.35it/s]


 16%|█▌        | 21882/138493 [01:00<05:07, 378.83it/s]


 16%|█▌       

...

 83%|████████▎ | 115638/138493 [05:34<01:13, 309.66it/s]


 84%|████████▎ | 115686/138493 [05:34<01:06, 341.47it/s]


 84%|████████▎ | 115747/138493 [05:34<00:57, 393.12it/s]


 84%|████████▎ | 115792/138493 [05:34<00:56, 405.25it/s]


 84%|████████▎ | 115837/138493 [05:34<01:06, 340.13it/s]


 84%|████████▎ | 115876/138493 [05:34<01:24, 269.06it/s]


 84%|████████▎ | 115928/138493 [05:34<01:12, 310.42it/s]


 84%|████████▎ | 115982/138493 [05:34<01:05, 345.29it/s]


 84%|████████▍ | 116030/138493 [05:35<01:00, 374.07it/s]


 84%|████████▍ | 116072/138493 [05:35<00:59, 379.08it/s]


 84%|████████▍ | 116114/138493 [05:35<00:58, 385.74it/s]


 84%|████████▍ | 116155/138493 [05:35<00:57, 389.67it/s]


 84%|████████▍ | 116196/138493 [05:35<00:58, 379.41it/s]


 84%|████████▍ | 116241/138493 [05:35<00:58, 381.18it/s]


 84%|████████▍ | 116280/138493 [05:35<01:02, 354.67it/s]


 84%|████████▍ | 116317/138493 [05:35<01:18, 281.90it/s]


 84%|████████▍ | 116358/138493 [05:36<01:11, 309.42it/s]

 87%|████████▋ | 120943/138493 [05:48<00:50, 344.86it/s]


 87%|████████▋ | 120980/138493 [05:48<00:51, 338.10it/s]


 87%|████████▋ | 121024/138493 [05:48<00:50, 349.13it/s]


 87%|████████▋ | 121064/138493 [05:48<00:48, 356.46it/s]


 87%|████████▋ | 121124/138493 [05:48<00:42, 404.21it/s]


 87%|████████▋ | 121180/138493 [05:48<00:39, 439.09it/s]


 88%|████████▊ | 121227/138493 [05:49<00:39, 436.98it/s]


 88%|████████▊ | 121297/138493 [05:49<00:34, 492.14it/s]


 88%|████████▊ | 121350/138493 [05:49<00:40, 420.47it/s]


 88%|████████▊ | 121397/138493 [05:49<00:45, 373.83it/s]


 88%|████████▊ | 121439/138493 [05:49<00:45, 374.21it/s]


 88%|████████▊ | 121484/138493 [05:49<00:43, 392.05it/s]


 88%|████████▊ | 121526/138493 [05:49<00:42, 395.41it/s]


 88%|████████▊ | 121568/138493 [05:50<00:55, 307.59it/s]


 88%|████████▊ | 121620/138493 [05:50<00:48, 346.50it/s]


 88%|████████▊ | 121660/138493 [05:50<00:48, 345.28it/s]


 88%|████████▊ | 121706/138493 [05:50<00:45, 372.73it/s]

 91%|█████████ | 126085/138493 [06:03<00:39, 314.18it/s]


 91%|█████████ | 126132/138493 [06:03<00:35, 347.83it/s]


 91%|█████████ | 126177/138493 [06:03<00:34, 359.62it/s]


 91%|█████████ | 126228/138493 [06:03<00:34, 352.79it/s]


 91%|█████████ | 126269/138493 [06:03<00:35, 348.11it/s]


 91%|█████████ | 126308/138493 [06:03<00:33, 359.32it/s]


 91%|█████████ | 126370/138493 [06:04<00:29, 405.77it/s]


 91%|█████████▏| 126425/138493 [06:04<00:27, 438.96it/s]


 91%|█████████▏| 126472/138493 [06:04<00:27, 433.97it/s]


 91%|█████████▏| 126518/138493 [06:04<00:29, 412.33it/s]


 91%|█████████▏| 126561/138493 [06:04<00:29, 409.19it/s]


 91%|█████████▏| 126608/138493 [06:04<00:27, 425.28it/s]


 91%|█████████▏| 126658/138493 [06:04<00:26, 444.57it/s]


 91%|█████████▏| 126704/138493 [06:04<00:28, 414.82it/s]


 92%|█████████▏| 126747/138493 [06:04<00:29, 394.56it/s]


 92%|█████████▏| 126799/138493 [06:05<00:27, 423.85it/s]


 92%|█████████▏| 126862/138493 [06:05<00:25, 459.29it/s]

 95%|█████████▍| 131395/138493 [06:17<00:20, 338.10it/s]


 95%|█████████▍| 131433/138493 [06:17<00:20, 349.57it/s]


 95%|█████████▍| 131469/138493 [06:17<00:20, 337.72it/s]


 95%|█████████▍| 131507/138493 [06:17<00:19, 349.30it/s]


 95%|█████████▍| 131556/138493 [06:17<00:18, 379.25it/s]


 95%|█████████▌| 131604/138493 [06:17<00:17, 404.50it/s]


 95%|█████████▌| 131646/138493 [06:17<00:17, 384.92it/s]


 95%|█████████▌| 131686/138493 [06:18<00:18, 365.47it/s]


 95%|█████████▌| 131724/138493 [06:18<00:18, 358.41it/s]


 95%|█████████▌| 131761/138493 [06:19<00:19, 345.17it/s]


 95%|█████████▌| 131797/138493 [06:19<01:05, 103.00it/s]


 95%|█████████▌| 131845/138493 [06:19<00:49, 134.73it/s]


 95%|█████████▌| 131894/138493 [06:19<00:39, 165.51it/s]


 95%|█████████▌| 131928/138493 [06:19<00:39, 166.14it/s]


 95%|█████████▌| 131961/138493 [06:19<00:34, 188.65it/s]


 95%|█████████▌| 132020/138493 [06:19<00:27, 236.58it/s]


 95%|█████████▌| 132058/138493 [06:20<00:24, 261.58it/s]

 99%|█████████▊| 136751/138493 [06:32<00:04, 380.88it/s]


 99%|█████████▉| 136794/138493 [06:32<00:04, 389.88it/s]


 99%|█████████▉| 136835/138493 [06:32<00:04, 383.73it/s]


 99%|█████████▉| 136875/138493 [06:32<00:04, 369.35it/s]


 99%|█████████▉| 136914/138493 [06:32<00:04, 363.23it/s]


 99%|█████████▉| 136952/138493 [06:32<00:04, 364.32it/s]


 99%|█████████▉| 136989/138493 [06:32<00:04, 338.60it/s]


 99%|█████████▉| 137024/138493 [06:33<00:04, 341.37it/s]


 99%|█████████▉| 137059/138493 [06:33<00:04, 318.32it/s]


 99%|█████████▉| 137115/138493 [06:33<00:03, 365.60it/s]


 99%|█████████▉| 137155/138493 [06:33<00:03, 369.52it/s]


 99%|█████████▉| 137202/138493 [06:33<00:03, 357.92it/s]


 99%|█████████▉| 137246/138493 [06:33<00:03, 378.94it/s]


 99%|█████████▉| 137286/138493 [06:33<00:03, 312.53it/s]


 99%|█████████▉| 137321/138493 [06:33<00:03, 303.31it/s]


 99%|█████████▉| 137358/138493 [06:34<00:03, 316.00it/s]


 99%|█████████▉| 137392/138493 [06:34<00:03, 304.44it/s]

In [28]:
num_train_negs

516458359

In [29]:
test_negs, num_test_negs = NegativeSampling(user_items_train, items, 1)




  0%|          | 0/138493 [00:00<?, ?it/s]


  0%|          | 560/138493 [00:00<00:24, 5598.00it/s]


  1%|          | 1470/138493 [00:00<00:21, 6328.18it/s]


  1%|▏         | 1861/138493 [00:00<01:19, 1713.50it/s]


  2%|▏         | 2772/138493 [00:00<00:59, 2264.74it/s]


  3%|▎         | 3639/138493 [00:01<00:46, 2909.43it/s]


  3%|▎         | 4507/138493 [00:01<00:36, 3631.07it/s]


  4%|▍         | 5451/138493 [00:01<00:29, 4452.95it/s]


  5%|▍         | 6349/138493 [00:01<00:25, 5245.12it/s]


  5%|▌         | 7348/138493 [00:01<00:21, 6115.51it/s]


  6%|▌         | 8319/138493 [00:01<00:18, 6879.34it/s]


  7%|▋         | 9211/138493 [00:01<00:17, 7233.23it/s]


  7%|▋         | 10082/138493 [00:01<00:18, 7028.49it/s]


  8%|▊         | 10954/138493 [00:01<00:17, 7461.95it/s]


  9%|▊         | 11900/138493 [00:01<00:15, 7961.47it/s]


  9%|▉         | 12789/138493 [00:02<00:15, 8214.11it/s]


 10%|▉         | 13753/138493 [00:02<00:14, 8594.40it/s]


 11%|█         | 146

 80%|███████▉  | 110787/138493 [00:31<00:02, 9546.65it/s]


 81%|████████  | 111744/138493 [00:31<00:03, 8707.07it/s]


 81%|████████▏ | 112701/138493 [00:31<00:02, 8948.15it/s]


 82%|████████▏ | 113641/138493 [00:31<00:02, 9077.80it/s]


 83%|████████▎ | 114559/138493 [00:31<00:02, 8947.04it/s]


 83%|████████▎ | 115499/138493 [00:31<00:02, 9075.78it/s]


 84%|████████▍ | 116412/138493 [00:31<00:02, 9048.56it/s]


 85%|████████▍ | 117365/138493 [00:31<00:02, 9186.54it/s]


 85%|████████▌ | 118299/138493 [00:32<00:02, 9231.83it/s]


 86%|████████▌ | 119225/138493 [00:32<00:02, 8234.47it/s]


 87%|████████▋ | 120143/138493 [00:32<00:02, 8496.70it/s]


 87%|████████▋ | 121075/138493 [00:32<00:01, 8727.49it/s]


 88%|████████▊ | 122027/138493 [00:32<00:01, 8947.94it/s]


 89%|████████▉ | 122952/138493 [00:32<00:01, 9031.07it/s]


 89%|████████▉ | 123926/138493 [00:32<00:01, 9227.40it/s]


 90%|█████████ | 124856/138493 [00:32<00:01, 9165.97it/s]


 91%|█████████ | 125820/138493 [00:32<00

In [30]:
len(train_negs)

138493

In [31]:
# write to array
train_data_neg = np.zeros((num_train_negs,3), dtype=int)
idx = 0
for user in tqdm(train_negs):
    for j in train_negs[user]:
        train_data_neg[idx, 0] = user
        train_data_neg[idx, 1] = j
        train_data_neg[idx, 2] = 0
        idx += 1




  0%|          | 0/138493 [00:00<?, ?it/s]


  0%|          | 70/138493 [00:00<03:20, 691.50it/s]


  0%|          | 132/138493 [00:00<03:28, 664.25it/s]


  0%|          | 205/138493 [00:00<03:22, 681.61it/s]


  0%|          | 266/138493 [00:00<03:30, 655.17it/s]


  0%|          | 320/138493 [00:00<03:44, 614.60it/s]


  0%|          | 378/138493 [00:00<03:50, 599.66it/s]


  0%|          | 431/138493 [00:00<04:17, 536.04it/s]


  0%|          | 488/138493 [00:00<04:14, 543.28it/s]


  0%|          | 561/138493 [00:00<03:54, 588.38it/s]


  0%|          | 619/138493 [00:01<04:02, 568.91it/s]


  0%|          | 676/138493 [00:01<04:02, 567.24it/s]


  1%|          | 735/138493 [00:01<04:02, 568.96it/s]


  1%|          | 792/138493 [00:01<04:16, 537.69it/s]


  1%|          | 861/138493 [00:01<03:59, 575.63it/s]


  1%|          | 920/138493 [00:01<03:58, 576.25it/s]


  1%|          | 979/138493 [00:01<04:00, 570.63it/s]


  1%|          | 1037/138493 [00:01<04:01, 570.17it/s]




  6%|▌         | 7815/138493 [00:13<03:51, 564.55it/s]


  6%|▌         | 7877/138493 [00:13<03:45, 578.84it/s]


  6%|▌         | 7940/138493 [00:13<03:42, 587.54it/s]


  6%|▌         | 8006/138493 [00:13<03:35, 606.86it/s]


  6%|▌         | 8068/138493 [00:13<03:42, 587.37it/s]


  6%|▌         | 8128/138493 [00:13<03:43, 583.31it/s]


  6%|▌         | 8187/138493 [00:13<03:44, 579.24it/s]


  6%|▌         | 8246/138493 [00:14<03:48, 570.96it/s]


  6%|▌         | 8315/138493 [00:14<03:36, 600.30it/s]


  6%|▌         | 8384/138493 [00:14<03:28, 623.59it/s]


  6%|▌         | 8447/138493 [00:14<03:46, 575.13it/s]


  6%|▌         | 8506/138493 [00:14<03:46, 573.61it/s]


  6%|▌         | 8568/138493 [00:14<03:45, 577.10it/s]


  6%|▌         | 8627/138493 [00:14<03:47, 570.29it/s]


  6%|▋         | 8685/138493 [00:14<03:54, 554.50it/s]


  6%|▋         | 8758/138493 [00:14<03:38, 593.00it/s]


  6%|▋         | 8819/138493 [00:15<03:39, 591.46it/s]


  6%|▋         | 8896/138493 [0

 11%|█         | 15573/138493 [00:26<03:38, 562.14it/s]


 11%|█▏        | 15631/138493 [00:26<03:40, 556.40it/s]


 11%|█▏        | 15700/138493 [00:26<03:28, 590.06it/s]


 11%|█▏        | 15760/138493 [00:26<03:37, 563.60it/s]


 11%|█▏        | 15822/138493 [00:26<03:36, 567.59it/s]


 11%|█▏        | 15882/138493 [00:27<03:34, 572.91it/s]


 12%|█▏        | 15940/138493 [00:27<03:44, 545.01it/s]


 12%|█▏        | 16008/138493 [00:27<03:31, 579.33it/s]


 12%|█▏        | 16067/138493 [00:27<03:38, 560.47it/s]


 12%|█▏        | 16126/138493 [00:27<03:35, 568.09it/s]


 12%|█▏        | 16184/138493 [00:27<03:56, 516.59it/s]


 12%|█▏        | 16238/138493 [00:27<03:58, 512.92it/s]


 12%|█▏        | 16297/138493 [00:27<03:49, 532.61it/s]


 12%|█▏        | 16352/138493 [00:27<03:47, 537.16it/s]


 12%|█▏        | 16421/138493 [00:28<03:32, 575.30it/s]


 12%|█▏        | 16480/138493 [00:28<03:30, 579.39it/s]


 12%|█▏        | 16539/138493 [00:28<03:29, 581.08it/s]


 12%|█▏       

 17%|█▋        | 23341/138493 [00:39<03:47, 506.70it/s]


 17%|█▋        | 23408/138493 [00:39<03:30, 546.63it/s]


 17%|█▋        | 23465/138493 [00:40<03:36, 531.16it/s]


 17%|█▋        | 23520/138493 [00:40<03:34, 536.44it/s]


 17%|█▋        | 23583/138493 [00:40<03:24, 561.39it/s]


 17%|█▋        | 23640/138493 [00:40<03:23, 563.54it/s]


 17%|█▋        | 23700/138493 [00:40<03:21, 571.04it/s]


 17%|█▋        | 23759/138493 [00:40<03:19, 574.49it/s]


 17%|█▋        | 23825/138493 [00:40<03:11, 597.29it/s]


 17%|█▋        | 23886/138493 [00:40<03:21, 569.16it/s]


 17%|█▋        | 23946/138493 [00:40<03:18, 577.13it/s]


 17%|█▋        | 24008/138493 [00:40<03:17, 578.66it/s]


 17%|█▋        | 24071/138493 [00:41<03:14, 587.33it/s]


 17%|█▋        | 24130/138493 [00:41<03:20, 569.75it/s]


 17%|█▋        | 24189/138493 [00:41<03:19, 572.47it/s]


 18%|█▊        | 24247/138493 [00:41<03:32, 537.30it/s]


 18%|█▊        | 24317/138493 [00:41<03:18, 575.35it/s]


 18%|█▊       

 22%|██▏       | 30958/138493 [00:52<02:56, 609.72it/s]


 22%|██▏       | 31020/138493 [00:53<02:56, 610.51it/s]


 22%|██▏       | 31098/138493 [00:53<02:45, 649.58it/s]


 23%|██▎       | 31164/138493 [00:53<02:50, 630.11it/s]


 23%|██▎       | 31228/138493 [00:53<02:58, 599.78it/s]


 23%|██▎       | 31295/138493 [00:53<02:54, 615.49it/s]


 23%|██▎       | 31358/138493 [00:53<03:00, 592.38it/s]


 23%|██▎       | 31425/138493 [00:53<02:54, 612.88it/s]


 23%|██▎       | 31491/138493 [00:53<02:50, 625.85it/s]


 23%|██▎       | 31575/138493 [00:53<02:38, 674.06it/s]


 23%|██▎       | 31644/138493 [00:54<02:43, 655.50it/s]


 23%|██▎       | 31711/138493 [00:54<02:47, 636.05it/s]


 23%|██▎       | 31776/138493 [00:54<03:00, 591.00it/s]


 23%|██▎       | 31845/138493 [00:54<02:53, 614.20it/s]


 23%|██▎       | 31908/138493 [00:54<02:56, 603.53it/s]


 23%|██▎       | 31978/138493 [00:54<02:50, 626.48it/s]


 23%|██▎       | 32045/138493 [00:54<02:46, 637.75it/s]


 23%|██▎      

...

 73%|███████▎  | 100473/138493 [02:52<01:10, 541.78it/s]


 73%|███████▎  | 100536/138493 [02:52<01:07, 565.21it/s]


 73%|███████▎  | 100594/138493 [02:52<01:08, 550.41it/s]


 73%|███████▎  | 100650/138493 [02:52<01:13, 511.44it/s]


 73%|███████▎  | 100712/138493 [02:52<01:11, 529.36it/s]


 73%|███████▎  | 100781/138493 [02:53<01:06, 564.49it/s]


 73%|███████▎  | 100842/138493 [02:53<01:05, 576.49it/s]


 73%|███████▎  | 100922/138493 [02:53<00:59, 628.56it/s]


 73%|███████▎  | 100987/138493 [02:53<01:03, 589.07it/s]


 73%|███████▎  | 101048/138493 [02:53<01:06, 563.46it/s]


 73%|███████▎  | 101114/138493 [02:53<01:03, 588.56it/s]


 73%|███████▎  | 101175/138493 [02:53<01:06, 557.42it/s]


 73%|███████▎  | 101241/138493 [02:53<01:03, 584.45it/s]


 73%|███████▎  | 101301/138493 [02:53<01:04, 576.15it/s]


 73%|███████▎  | 101368/138493 [02:54<01:01, 598.91it/s]


 73%|███████▎  | 101429/138493 [02:54<01:01, 600.40it/s]


 73%|███████▎  | 101495/138493 [02:54<01:02, 591.43it/s]

 78%|███████▊  | 108180/138493 [03:05<00:57, 528.87it/s]


 78%|███████▊  | 108235/138493 [03:05<00:57, 524.76it/s]


 78%|███████▊  | 108295/138493 [03:05<00:55, 543.42it/s]


 78%|███████▊  | 108359/138493 [03:05<00:53, 568.54it/s]


 78%|███████▊  | 108417/138493 [03:05<00:54, 549.99it/s]


 78%|███████▊  | 108473/138493 [03:06<00:56, 530.30it/s]


 78%|███████▊  | 108538/138493 [03:06<00:53, 556.89it/s]


 78%|███████▊  | 108595/138493 [03:06<00:55, 542.94it/s]


 78%|███████▊  | 108652/138493 [03:06<00:54, 548.42it/s]


 79%|███████▊  | 108721/138493 [03:06<00:51, 583.72it/s]


 79%|███████▊  | 108781/138493 [03:06<00:51, 571.76it/s]


 79%|███████▊  | 108850/138493 [03:06<00:49, 594.95it/s]


 79%|███████▊  | 108911/138493 [03:06<00:50, 580.38it/s]


 79%|███████▊  | 108971/138493 [03:06<00:50, 584.56it/s]


 79%|███████▊  | 109030/138493 [03:07<00:52, 558.21it/s]


 79%|███████▉  | 109091/138493 [03:07<00:51, 570.95it/s]


 79%|███████▉  | 109152/138493 [03:07<00:50, 576.34it/s]

 84%|████████▎ | 115798/138493 [03:18<00:38, 588.74it/s]


 84%|████████▎ | 115859/138493 [03:18<00:43, 519.77it/s]


 84%|████████▎ | 115928/138493 [03:18<00:40, 554.98it/s]


 84%|████████▍ | 116001/138493 [03:18<00:38, 591.79it/s]


 84%|████████▍ | 116063/138493 [03:19<00:38, 587.74it/s]


 84%|████████▍ | 116127/138493 [03:19<00:37, 591.40it/s]


 84%|████████▍ | 116189/138493 [03:19<00:37, 587.80it/s]


 84%|████████▍ | 116253/138493 [03:19<00:37, 600.27it/s]


 84%|████████▍ | 116314/138493 [03:19<00:39, 558.40it/s]


 84%|████████▍ | 116371/138493 [03:19<00:40, 539.88it/s]


 84%|████████▍ | 116436/138493 [03:19<00:39, 562.90it/s]


 84%|████████▍ | 116498/138493 [03:19<00:38, 564.17it/s]


 84%|████████▍ | 116556/138493 [03:19<00:39, 551.94it/s]


 84%|████████▍ | 116612/138493 [03:20<00:39, 547.97it/s]


 84%|████████▍ | 116668/138493 [03:20<00:40, 540.34it/s]


 84%|████████▍ | 116731/138493 [03:20<00:38, 562.64it/s]


 84%|████████▍ | 116802/138493 [03:20<00:36, 599.23it/s]

 89%|████████▉ | 123421/138493 [03:31<00:27, 543.20it/s]


 89%|████████▉ | 123498/138493 [03:31<00:25, 594.11it/s]


 89%|████████▉ | 123571/138493 [03:31<00:23, 627.75it/s]


 89%|████████▉ | 123637/138493 [03:32<00:23, 631.66it/s]


 89%|████████▉ | 123703/138493 [03:32<00:25, 585.12it/s]


 89%|████████▉ | 123764/138493 [03:32<00:27, 539.70it/s]


 89%|████████▉ | 123821/138493 [03:32<00:27, 532.81it/s]


 89%|████████▉ | 123889/138493 [03:32<00:25, 566.94it/s]


 89%|████████▉ | 123949/138493 [03:32<00:25, 569.77it/s]


 90%|████████▉ | 124008/138493 [03:32<00:25, 570.11it/s]


 90%|████████▉ | 124078/138493 [03:32<00:24, 600.25it/s]


 90%|████████▉ | 124140/138493 [03:32<00:25, 571.06it/s]


 90%|████████▉ | 124199/138493 [03:33<00:25, 569.84it/s]


 90%|████████▉ | 124258/138493 [03:33<00:25, 568.96it/s]


 90%|████████▉ | 124321/138493 [03:33<00:24, 572.67it/s]


 90%|████████▉ | 124379/138493 [03:33<00:25, 561.94it/s]


 90%|████████▉ | 124442/138493 [03:33<00:24, 579.50it/s]

 95%|█████████▍| 131066/138493 [03:44<00:13, 538.96it/s]


 95%|█████████▍| 131129/138493 [03:44<00:13, 562.08it/s]


 95%|█████████▍| 131187/138493 [03:44<00:14, 515.27it/s]


 95%|█████████▍| 131242/138493 [03:44<00:13, 519.34it/s]


 95%|█████████▍| 131296/138493 [03:45<00:13, 519.97it/s]


 95%|█████████▍| 131349/138493 [03:45<00:13, 513.09it/s]


 95%|█████████▍| 131407/138493 [03:45<00:13, 529.44it/s]


 95%|█████████▍| 131467/138493 [03:45<00:12, 542.47it/s]


 95%|█████████▍| 131527/138493 [03:45<00:12, 558.47it/s]


 95%|█████████▌| 131598/138493 [03:45<00:11, 596.13it/s]


 95%|█████████▌| 131659/138493 [03:45<00:11, 597.01it/s]


 95%|█████████▌| 131720/138493 [03:45<00:11, 597.75it/s]


 95%|█████████▌| 131781/138493 [03:45<00:11, 569.64it/s]


 95%|█████████▌| 131853/138493 [03:46<00:10, 607.53it/s]


 95%|█████████▌| 131915/138493 [03:46<00:11, 556.41it/s]


 95%|█████████▌| 131980/138493 [03:46<00:11, 579.35it/s]


 95%|█████████▌| 132052/138493 [03:46<00:10, 608.91it/s]

In [32]:
# test negative data
test_data_neg = np.zeros((num_test_negs,3), dtype=int)
idx = 0
for user in tqdm(test_negs):
    for j in test_negs[user]:
        test_data_neg[idx, 0] = user
        test_data_neg[idx, 1] = j
        test_data_neg[idx, 2] = 0
        idx += 1




  0%|          | 0/138493 [00:00<?, ?it/s]


  1%|          | 1470/138493 [00:00<00:09, 14689.30it/s]


  2%|▏         | 2857/138493 [00:00<00:09, 14432.86it/s]


  3%|▎         | 4222/138493 [00:00<00:09, 14156.72it/s]


  4%|▍         | 5633/138493 [00:00<00:09, 14141.45it/s]


  5%|▌         | 7201/138493 [00:00<00:09, 14564.96it/s]


  6%|▌         | 8636/138493 [00:00<00:08, 14486.38it/s]


  7%|▋         | 10047/138493 [00:00<00:08, 14370.71it/s]


  8%|▊         | 11482/138493 [00:00<00:08, 14363.08it/s]


  9%|▉         | 12910/138493 [00:00<00:08, 14337.98it/s]


 10%|█         | 14343/138493 [00:01<00:08, 14334.98it/s]


 11%|█▏        | 15768/138493 [00:01<00:08, 14302.77it/s]


 12%|█▏        | 17211/138493 [00:01<00:08, 14340.26it/s]


 13%|█▎        | 18645/138493 [00:01<00:08, 14339.38it/s]


 15%|█▍        | 20132/138493 [00:01<00:08, 14428.98it/s]


 16%|█▌        | 21686/138493 [00:01<00:07, 14744.41it/s]


 17%|█▋        | 23167/138493 [00:01<00:07, 14763.26it/s]


In [33]:
num_test_negs

19842772

In [34]:
train_data_np= np.concatenate([train_data_neg, train_data.values])
np.random.shuffle(train_data_np)

test_data_np= np.concatenate([test_data_neg, test_data.values])
np.random.shuffle(test_data_np)

In [35]:
np.sum(test_data_np[:,2])

138493

In [36]:
test_data_np

array([[ 65091,  44947,      0],
       [101639,   3441,      0],
       [117858, 111285,      0],
       ...,
       [119746,  27778,      0],
       [ 96283,   1437,      0],
       [ 92125,  52838,      0]])

# Write to text file

In [37]:
rd = np.random.randint(0, 100, size=(100000,1))
def write_DLRM_data(data, filename='dlrm_data.tsv'):
    print("Writing %d samples"%data.shape[0], filename)
    with open(filename, 'wt') as f:
        for i in tqdm(range(data.shape[0])):
            f.write('%d\t%d\t%d\t%d\n'%(data[i,2], rd[i%100000], data[i,0], data[i,1])) #label, dummy numeric feat., userID, itemID

In [38]:
!rm -rf /data/dlrm/
!mkdir -p /data/dlrm/criteo
for i, data_arr in enumerate(np.array_split(train_data_np,23)):
    write_DLRM_data(data_arr, filename='/data/dlrm/criteo/day_%d'%i)




  0%|          | 0/23318267 [00:00<?, ?it/s]

Writing 23318267 samples /data/dlrm/criteo/day_0





  0%|          | 57404/23318267 [00:00<00:40, 574035.07it/s]


  0%|          | 113922/23318267 [00:00<00:40, 571346.83it/s]


  1%|          | 172618/23318267 [00:00<00:40, 575942.62it/s]


  1%|          | 231022/23318267 [00:00<00:39, 578346.27it/s]


  1%|          | 290905/23318267 [00:00<00:39, 584341.67it/s]


  1%|▏         | 349699/23318267 [00:00<00:39, 585413.36it/s]


  2%|▏         | 410353/23318267 [00:00<00:38, 591592.05it/s]


  2%|▏         | 471274/23318267 [00:00<00:38, 596768.42it/s]


  2%|▏         | 529935/23318267 [00:00<00:38, 593682.17it/s]


  3%|▎         | 589692/23318267 [00:01<00:38, 594840.40it/s]


  3%|▎         | 650766/23318267 [00:01<00:37, 599519.47it/s]


  3%|▎         | 710390/23318267 [00:01<00:37, 598531.16it/s]


  3%|▎         | 770028/23318267 [00:01<00:37, 597881.36it/s]


  4%|▎         | 829305/23318267 [00:01<00:37, 596336.74it/s]


  4%|▍         | 889643/23318267 [00:01<00:37, 598431.29it/s]


  4%|▍         | 949222/23318267 [00:0

 29%|██▊       | 6701290/23318267 [00:11<00:27, 607984.00it/s]


 29%|██▉       | 6762100/23318267 [00:11<00:27, 600293.61it/s]


 29%|██▉       | 6822160/23318267 [00:11<00:27, 597344.27it/s]


 30%|██▉       | 6881919/23318267 [00:11<00:27, 592218.40it/s]


 30%|██▉       | 6942415/23318267 [00:11<00:27, 595983.08it/s]


 30%|███       | 7002199/23318267 [00:11<00:27, 596536.13it/s]


 30%|███       | 7064285/23318267 [00:11<00:26, 603629.28it/s]


 31%|███       | 7125179/23318267 [00:11<00:26, 605212.49it/s]


 31%|███       | 7186877/23318267 [00:12<00:26, 607274.09it/s]


 31%|███       | 7247771/23318267 [00:12<00:26, 607772.21it/s]


 31%|███▏      | 7309694/23318267 [00:12<00:26, 611163.66it/s]


 32%|███▏      | 7370824/23318267 [00:12<00:26, 607846.69it/s]


 32%|███▏      | 7431852/23318267 [00:12<00:26, 608573.08it/s]


 32%|███▏      | 7492763/23318267 [00:12<00:25, 608733.36it/s]


 32%|███▏      | 7553644/23318267 [00:12<00:26, 605018.82it/s]


 33%|███▎      | 7614634/

 58%|█████▊    | 13417419/23318267 [00:22<00:16, 599553.62it/s]


 58%|█████▊    | 13477393/23318267 [00:22<00:16, 590622.42it/s]


 58%|█████▊    | 13539899/23318267 [00:22<00:16, 600546.66it/s]


 58%|█████▊    | 13600414/23318267 [00:22<00:16, 601919.18it/s]


 59%|█████▊    | 13660656/23318267 [00:22<00:16, 596520.97it/s]


 59%|█████▉    | 13720355/23318267 [00:22<00:16, 595832.05it/s]


 59%|█████▉    | 13781409/23318267 [00:22<00:15, 600169.23it/s]


 59%|█████▉    | 13841457/23318267 [00:23<00:15, 599096.20it/s]


 60%|█████▉    | 13902387/23318267 [00:23<00:15, 602118.89it/s]


 60%|█████▉    | 13962618/23318267 [00:23<00:15, 600833.28it/s]


 60%|██████    | 14023282/23318267 [00:23<00:15, 602562.48it/s]


 60%|██████    | 14083550/23318267 [00:23<00:15, 595460.26it/s]


 61%|██████    | 14146380/23318267 [00:23<00:15, 604943.65it/s]


 61%|██████    | 14207822/23318267 [00:23<00:14, 607755.46it/s]


 61%|██████    | 14270193/23318267 [00:23<00:14, 612453.91it/s]


 61%|█████

...

Writing 23318266 samples /data/dlrm/criteo/day_22





  1%|          | 121250/23318266 [00:00<00:38, 608951.63it/s]


  1%|          | 180113/23318266 [00:00<00:38, 602706.85it/s]


  1%|          | 236419/23318266 [00:00<00:39, 590238.41it/s]


  1%|▏         | 297031/23318266 [00:00<00:38, 594912.47it/s]


  2%|▏         | 358957/23318266 [00:00<00:38, 602013.05it/s]


  2%|▏         | 419765/23318266 [00:00<00:37, 603818.41it/s]


  2%|▏         | 480695/23318266 [00:00<00:37, 605450.09it/s]


  2%|▏         | 541926/23318266 [00:00<00:37, 607491.61it/s]


  3%|▎         | 602364/23318266 [00:01<00:37, 606553.20it/s]


  3%|▎         | 665004/23318266 [00:01<00:36, 612372.81it/s]


  3%|▎         | 726071/23318266 [00:01<00:36, 611858.95it/s]


  3%|▎         | 788750/23318266 [00:01<00:36, 616261.04it/s]


  4%|▎         | 849894/23318266 [00:01<00:36, 614803.85it/s]


  4%|▍         | 912899/23318266 [00:01<00:36, 619296.78it/s]


  4%|▍         | 974556/23318266 [00:01<00:36, 614975.71it/s]


  4%|▍         | 1037739/23318266 [00

 30%|██▉       | 6919088/23318266 [00:11<00:26, 620266.09it/s]


 30%|██▉       | 6981129/23318266 [00:11<00:26, 614938.56it/s]


 30%|███       | 7044449/23318266 [00:11<00:26, 620303.86it/s]


 30%|███       | 7106505/23318266 [00:11<00:26, 619879.55it/s]


 31%|███       | 7168511/23318266 [00:11<00:26, 618651.76it/s]


 31%|███       | 7230390/23318266 [00:11<00:26, 618340.09it/s]


 31%|███▏      | 7292234/23318266 [00:11<00:26, 609667.30it/s]


 32%|███▏      | 7353511/23318266 [00:12<00:26, 610591.93it/s]


 32%|███▏      | 7416791/23318266 [00:12<00:25, 617086.96it/s]


 32%|███▏      | 7478534/23318266 [00:12<00:25, 616469.80it/s]


 32%|███▏      | 7540205/23318266 [00:12<00:25, 609084.83it/s]


 33%|███▎      | 7603103/23318266 [00:12<00:25, 614917.12it/s]


 33%|███▎      | 7665185/23318266 [00:12<00:25, 616675.90it/s]


 33%|███▎      | 7726881/23318266 [00:12<00:25, 616644.88it/s]


 33%|███▎      | 7788566/23318266 [00:12<00:25, 609364.62it/s]


 34%|███▎      | 7851291/

 59%|█████▉    | 13713470/23318266 [00:22<00:15, 609064.78it/s]


 59%|█████▉    | 13776297/23318266 [00:22<00:15, 614699.51it/s]


 59%|█████▉    | 13839532/23318266 [00:22<00:15, 619887.89it/s]


 60%|█████▉    | 13901605/23318266 [00:22<00:15, 617770.35it/s]


 60%|█████▉    | 13964546/23318266 [00:22<00:15, 621216.09it/s]


 60%|██████    | 14027419/23318266 [00:22<00:14, 623449.30it/s]


 60%|██████    | 14089799/23318266 [00:22<00:14, 622285.74it/s]


 61%|██████    | 14152638/23318266 [00:23<00:14, 624102.93it/s]


 61%|██████    | 14215651/23318266 [00:23<00:14, 625895.53it/s]


 61%|██████    | 14278255/23318266 [00:23<00:14, 624646.27it/s]


 62%|██████▏   | 14340759/23318266 [00:23<00:14, 624762.28it/s]


 62%|██████▏   | 14403476/23318266 [00:23<00:14, 625481.49it/s]


 62%|██████▏   | 14466679/23318266 [00:23<00:14, 627429.26it/s]


 62%|██████▏   | 14529771/23318266 [00:23<00:13, 628471.25it/s]


 63%|██████▎   | 14593062/23318266 [00:23<00:13, 629793.37it/s]


 63%|█████

 88%|████████▊ | 20489411/23318266 [00:33<00:04, 600728.09it/s]


 88%|████████▊ | 20551196/23318266 [00:33<00:04, 605763.50it/s]


 88%|████████▊ | 20614048/23318266 [00:33<00:04, 612412.71it/s]


 89%|████████▊ | 20675836/23318266 [00:33<00:04, 608398.01it/s]


 89%|████████▉ | 20738698/23318266 [00:34<00:04, 614324.27it/s]


 89%|████████▉ | 20800468/23318266 [00:34<00:04, 615332.40it/s]


 89%|████████▉ | 20862202/23318266 [00:34<00:03, 615590.39it/s]


 90%|████████▉ | 20924149/23318266 [00:34<00:03, 616747.58it/s]


 90%|████████▉ | 20985923/23318266 [00:34<00:03, 612037.96it/s]


 90%|█████████ | 21047662/23318266 [00:34<00:03, 613633.10it/s]


 91%|█████████ | 21110306/23318266 [00:34<00:03, 617418.28it/s]


 91%|█████████ | 21172207/23318266 [00:34<00:03, 617892.03it/s]


 91%|█████████ | 21234028/23318266 [00:34<00:03, 600421.03it/s]


 91%|█████████▏| 21295491/23318266 [00:34<00:03, 604613.58it/s]


 92%|█████████▏| 21356651/23318266 [00:35<00:03, 606689.85it/s]


 92%|█████

In [39]:
!head /data/dlrm/criteo/day_0

0	37	91113	61493
0	89	22313	87751
0	60	134203	95302
0	34	92518	45208
0	54	46555	5869
0	81	30960	6140
0	33	48668	62378
0	1	9469	813
0	1	19670	1552
0	70	131943	68647


In [40]:
write_DLRM_data(test_data_np, filename='/data/dlrm/criteo/day_23')




  0%|          | 0/19981265 [00:00<?, ?it/s]




Writing 19981265 samples /data/dlrm/criteo/day_23


  0%|          | 57469/19981265 [00:00<00:34, 574689.18it/s]


  1%|          | 115814/19981265 [00:00<00:34, 577287.80it/s]


  1%|          | 173867/19981265 [00:00<00:34, 578256.40it/s]


  1%|          | 230670/19981265 [00:00<00:34, 575147.28it/s]


  1%|▏         | 290691/19981265 [00:00<00:33, 582442.48it/s]


  2%|▏         | 349769/19981265 [00:00<00:33, 584916.60it/s]


  2%|▏         | 409246/19981265 [00:00<00:33, 587835.43it/s]


  2%|▏         | 470637/19981265 [00:00<00:32, 595421.57it/s]


  3%|▎         | 529868/19981265 [00:00<00:32, 594484.42it/s]


  3%|▎         | 591320/19981265 [00:01<00:32, 600356.31it/s]


  3%|▎         | 651077/19981265 [00:01<00:32, 591862.41it/s]


  4%|▎         | 711988/19981265 [00:01<00:32, 596929.65it/s]


  4%|▍         | 773648/19981265 [00:01<00:31, 602665.01it/s]


  4%|▍         | 833847/19981265 [00:01<00:31, 602459.93it/s]


  4%|▍         | 893789/19981265 [00:01<00:31, 601543.60it/s]


  5%|▍         | 955358/19981265 [00:01<0

 34%|███▎      | 6725204/19981265 [00:11<00:22, 600390.43it/s]


 34%|███▍      | 6786242/19981265 [00:11<00:21, 603352.12it/s]


 34%|███▍      | 6847927/19981265 [00:11<00:21, 607337.94it/s]


 35%|███▍      | 6909558/19981265 [00:11<00:21, 609999.16it/s]


 35%|███▍      | 6970575/19981265 [00:11<00:21, 608721.58it/s]


 35%|███▌      | 7032154/19981265 [00:11<00:21, 610824.75it/s]


 36%|███▌      | 7094662/19981265 [00:11<00:20, 615029.73it/s]


 36%|███▌      | 7156180/19981265 [00:11<00:20, 612088.82it/s]


 36%|███▌      | 7218726/19981265 [00:12<00:20, 616037.76it/s]


 36%|███▋      | 7280345/19981265 [00:12<00:20, 611666.51it/s]


 37%|███▋      | 7342544/19981265 [00:12<00:20, 614724.96it/s]


 37%|███▋      | 7404033/19981265 [00:12<00:20, 608792.35it/s]


 37%|███▋      | 7465427/19981265 [00:12<00:20, 610327.30it/s]


 38%|███▊      | 7526478/19981265 [00:12<00:20, 603053.23it/s]


 38%|███▊      | 7589259/19981265 [00:12<00:20, 610271.27it/s]


 38%|███▊      | 7651047/

 67%|██████▋   | 13440370/19981265 [00:22<00:10, 609419.18it/s]


 68%|██████▊   | 13503182/19981265 [00:22<00:10, 614908.61it/s]


 68%|██████▊   | 13564705/19981265 [00:22<00:10, 607163.25it/s]


 68%|██████▊   | 13626613/19981265 [00:22<00:10, 610686.98it/s]


 69%|██████▊   | 13689500/19981265 [00:22<00:10, 616029.39it/s]


 69%|██████▉   | 13751140/19981265 [00:22<00:10, 609522.50it/s]


 69%|██████▉   | 13813867/19981265 [00:23<00:10, 614739.71it/s]


 69%|██████▉   | 13875381/19981265 [00:23<00:10, 610334.57it/s]


 70%|██████▉   | 13938362/19981265 [00:23<00:09, 616049.29it/s]


 70%|███████   | 14000005/19981265 [00:23<00:09, 609782.02it/s]


 70%|███████   | 14061206/19981265 [00:23<00:09, 610447.14it/s]


 71%|███████   | 14122602/19981265 [00:23<00:09, 611494.33it/s]


 71%|███████   | 14183909/19981265 [00:23<00:09, 611965.92it/s]


 71%|███████▏  | 14245516/19981265 [00:23<00:09, 612217.88it/s]


 72%|███████▏  | 14307409/19981265 [00:23<00:09, 614215.92it/s]


 72%|█████

In [41]:
!head /data/dlrm/criteo/day_0

0	37	91113	61493
0	89	22313	87751
0	60	134203	95302
0	34	92518	45208
0	54	46555	5869
0	81	30960	6140
0	33	48668	62378
0	1	9469	813
0	1	19670	1552
0	70	131943	68647


In [42]:
!tail /data/dlrm/criteo/day_23

0	69	121796	26285
0	48	22550	105034
0	48	35927	118288
0	11	127700	103543
0	52	5365	3444
0	11	61142	8593
0	31	52637	91137
0	82	119746	27778
0	98	96283	1437
0	39	92125	52838


# Preprocessing with DLRM

In [43]:
%%bash
apt install psmisc
cd ./preproc
killall -9 java
bash ./prepare_dataset.sh

Reading package lists...
Building dependency tree...
Reading state information...
psmisc is already the newest version (23.1-1ubuntu0.1).
0 upgraded, 0 newly installed, 0 to remove and 32 not upgraded.
total 788K
4.0K -rwxrwxrwx 1 root  root 1.1K Aug 13 04:24 verify_criteo_downloaded.sh
4.0K drwxrwxrwx 2 root  root 4.0K Aug 14 02:17 .ipynb_checkpoints
8.0K -rwxrwxrwx 1 root  root 4.6K Aug 14 02:19 split_dataset.py
4.0K -rwxrwxrwx 1 root  root 2.4K Aug 14 02:19 prepare_dataset.sh
4.0K -rwxrwxrwx 1 root  root 3.2K Aug 14 02:20 parquet_to_binary.py
   0 -rwxrwxrwx 1 root  root    0 Aug 14 13:32 data_prep_model.pickle
8.0K -rwxrwxrwx 1 root  root 5.9K Aug 14 13:45 run_spark.sh
 20K -rwxrwxrwx 1 root  root  20K Aug 14 13:54 spark_data_utils.py
4.0K drwxrwxrwx 3 root  root 4.0K Aug 14 13:54 .
236K -rwxrwxrwx 1 root  root 236K Aug 15 12:07 submit_dict_log.txt
268K -rwxrwxrwx 1 root  root 265K Aug 15 12:08 submit_train_log.txt
112K -rwxrwxrwx 1 root  root 109K Aug 15 12:09 submit_test_log.txt




+ ls -ltrash
+ download_dir=/data/dlrm/criteo
+ ./verify_criteo_downloaded.sh /data/dlrm/criteo
++ download_dir=/data/dlrm/criteo
++ cd /data/dlrm/criteo
+++ seq 0 23
++ for i in $(seq 0 23)
++ filename=day_0
++ '[' -f day_0 ']'
++ echo 'day_0 exists, OK'
++ for i in $(seq 0 23)
++ filename=day_1
++ '[' -f day_1 ']'
++ echo 'day_1 exists, OK'
++ for i in $(seq 0 23)
++ filename=day_2
++ '[' -f day_2 ']'
++ echo 'day_2 exists, OK'
++ for i in $(seq 0 23)
++ filename=day_3
++ '[' -f day_3 ']'
++ echo 'day_3 exists, OK'
++ for i in $(seq 0 23)
++ filename=day_4
++ '[' -f day_4 ']'
++ echo 'day_4 exists, OK'
++ for i in $(seq 0 23)
++ filename=day_5
++ '[' -f day_5 ']'
++ echo 'day_5 exists, OK'
++ for i in $(seq 0 23)
++ filename=day_6
++ '[' -f day_6 ']'
++ echo 'day_6 exists, OK'
++ for i in $(seq 0 23)
++ filename=day_7
++ '[' -f day_7 ']'
++ echo 'day_7 exists, OK'
++ for i in $(seq 0 23)
++ filename=day_8
++ '[' -f day_8 ']'
++ echo 'day_8 exists, OK'
++ for i in $(seq 0 23)
++ fil

In [44]:
!cat /data/dlrm/binary_dataset/model_size.json


{
    "_c2": 138493,
    "_c3": 26744
}

# Training

In [45]:
%run /workspace/dlrm/dlrm/scripts/main.py \
--mode train \
--dataset /data/dlrm/binary_dataset/ \
--num_numerical_features 1 \
--base_device cuda \
--lr 0.1 \
--embedding_type joint \
--epochs 10 \
--batch_size=8192 \
--save_checkpoint_path ./movie_lens_model

Using the Volta-optimized dot interaction kernels
DLL 2020-08-15 14:59:31.395946 - PARAMETER logtostderr : False  alsologtostderr : False  log_dir :   v : 0  verbosity : 0  stderrthreshold : fatal  showprefixforinfo : True  run_with_pdb : False  pdb_post_mortem : False  run_with_profiling : False  profile_file : None  use_cprofile_for_profiling : True  only_check_args : False  mode : train  seed : 12345  batch_size : 8192  test_batch_size : 32768  lr : 0.1  epochs : 10  max_steps : None  warmup_factor : 0  warmup_steps : 6400  decay_steps : 80000  decay_start_step : 64000  decay_power : 2  decay_end_lr : 0.0  embedding_type : joint  embedding_dim : 128  top_mlp_sizes : [1024, 1024, 512, 256, 1]  bottom_mlp_sizes : [512, 256, 128]  interaction_op : cuda_dot  dataset : /data/dlrm/binary_dataset/  dataset_type : split  synthetic_dataset_dir : /tmp/dlrm_sythetic_dataset  synthetic_dataset_table_sizes : ['100000', '100000', '100000', '100000', '100000', '100000', '100000', '100000', '100000

/workspace/dlrm/dlrm/data/datasets.py:213: UserWarning: The given NumPy array is not writeable, and PyTorch does not support non-writeable tensors. This means you can write to the underlying (supposedly non-writeable) NumPy array using the tensor. You may want to copy the array to protect its data or make it writeable before converting it to a tensor. This type of warning will be suppressed for the rest of this program. (Triggered internally at  ../torch/csrc/utils/tensor_numpy.cpp:141.)
  return torch.from_numpy(array).to(torch.float32)


Epoch:[0/10] [200/65469]  eta: 0:11:33  loss: 0.5116  step_time: 0.010631  lr: 0.0031
Epoch:[0/10] [400/65469]  eta: 0:10:36  loss: 0.2032  step_time: 0.008942  lr: 0.0063
Epoch:[0/10] [600/65469]  eta: 0:10:17  loss: 0.1694  step_time: 0.008972  lr: 0.0094
Epoch:[0/10] [800/65469]  eta: 0:10:07  loss: 0.1641  step_time: 0.009019  lr: 0.0125
Epoch:[0/10] [1000/65469]  eta: 0:10:00  loss: 0.1541  step_time: 0.008998  lr: 0.0156
Epoch:[0/10] [1200/65469]  eta: 0:09:55  loss: 0.1560  step_time: 0.009018  lr: 0.0188
Epoch:[0/10] [1400/65469]  eta: 0:09:51  loss: 0.1639  step_time: 0.009001  lr: 0.0219
Epoch:[0/10] [1600/65469]  eta: 0:09:47  loss: 0.1578  step_time: 0.009007  lr: 0.0250
Epoch:[0/10] [1800/65469]  eta: 0:09:44  loss: 0.1532  step_time: 0.009050  lr: 0.0281
Epoch:[0/10] [2000/65469]  eta: 0:09:42  loss: 0.1696  step_time: 0.009090  lr: 0.0313
Epoch:[0/10] [2200/65469]  eta: 0:09:39  loss: 0.1522  step_time: 0.009041  lr: 0.0344
Epoch:[0/10] [2400/65469]  eta: 0:09:37  loss: 

Epoch:[0/10] [19000/65469]  eta: 0:07:05  loss: 0.0832  step_time: 0.009209  lr: 0.1000
Epoch:[0/10] [19200/65469]  eta: 0:07:03  loss: 0.0808  step_time: 0.009220  lr: 0.1000
Epoch:[0/10] [19400/65469]  eta: 0:07:02  loss: 0.0796  step_time: 0.009163  lr: 0.1000
Epoch:[0/10] [19600/65469]  eta: 0:07:00  loss: 0.0884  step_time: 0.009207  lr: 0.1000
Epoch:[0/10] [19800/65469]  eta: 0:06:58  loss: 0.0794  step_time: 0.009213  lr: 0.1000
Epoch:[0/10] [20000/65469]  eta: 0:06:56  loss: 0.0830  step_time: 0.009191  lr: 0.1000
Epoch:[0/10] [20200/65469]  eta: 0:06:54  loss: 0.0750  step_time: 0.009173  lr: 0.1000
Epoch:[0/10] [20400/65469]  eta: 0:06:53  loss: 0.0766  step_time: 0.009344  lr: 0.1000
Epoch:[0/10] [20600/65469]  eta: 0:06:51  loss: 0.0915  step_time: 0.009349  lr: 0.1000
Epoch:[0/10] [20800/65469]  eta: 0:06:49  loss: 0.0914  step_time: 0.009243  lr: 0.1000
Epoch:[0/10] [21000/65469]  eta: 0:06:47  loss: 0.0747  step_time: 0.009166  lr: 0.1000
Epoch:[0/10] [21200/65469]  eta:

Epoch:[0/10] [37800/65469]  eta: 0:04:14  loss: 0.0715  step_time: 0.009306  lr: 0.1000
Epoch:[0/10] [38000/65469]  eta: 0:04:12  loss: 0.0749  step_time: 0.009208  lr: 0.1000
Epoch:[0/10] [38200/65469]  eta: 0:04:10  loss: 0.0755  step_time: 0.009226  lr: 0.1000
Epoch:[0/10] [38400/65469]  eta: 0:04:08  loss: 0.0829  step_time: 0.009227  lr: 0.1000
Epoch:[0/10] [38600/65469]  eta: 0:04:06  loss: 0.0770  step_time: 0.009210  lr: 0.1000
Epoch:[0/10] [38800/65469]  eta: 0:04:05  loss: 0.0803  step_time: 0.009208  lr: 0.1000
Epoch:[0/10] [39000/65469]  eta: 0:04:03  loss: 0.0792  step_time: 0.009197  lr: 0.1000
Epoch:[0/10] [39200/65469]  eta: 0:04:01  loss: 0.0731  step_time: 0.009202  lr: 0.1000
Epoch:[0/10] [39400/65469]  eta: 0:03:59  loss: 0.0810  step_time: 0.009205  lr: 0.1000
Epoch:[0/10] [39600/65469]  eta: 0:03:57  loss: 0.0776  step_time: 0.009204  lr: 0.1000
Epoch:[0/10] [39800/65469]  eta: 0:03:55  loss: 0.0811  step_time: 0.009215  lr: 0.1000
Epoch:[0/10] [40000/65469]  eta:

...

Epoch:[8/10] [46800/65469]  eta: 0:02:53  loss: 0.0723  step_time: 0.009210  lr: 0.0000
Epoch:[8/10] [47000/65469]  eta: 0:02:51  loss: 0.0775  step_time: 0.009210  lr: 0.0000
Epoch:[8/10] [47200/65469]  eta: 0:02:49  loss: 0.0790  step_time: 0.009241  lr: 0.0000
Epoch:[8/10] [47400/65469]  eta: 0:02:47  loss: 0.0812  step_time: 0.009205  lr: 0.0000
Epoch:[8/10] [47600/65469]  eta: 0:02:45  loss: 0.0739  step_time: 0.009217  lr: 0.0000
Epoch:[8/10] [47800/65469]  eta: 0:02:44  loss: 0.0750  step_time: 0.009214  lr: 0.0000
Epoch:[8/10] [48000/65469]  eta: 0:02:42  loss: 0.0799  step_time: 0.009339  lr: 0.0000
Epoch:[8/10] [48200/65469]  eta: 0:02:40  loss: 0.0793  step_time: 0.009384  lr: 0.0000
Epoch:[8/10] [48400/65469]  eta: 0:02:38  loss: 0.0821  step_time: 0.009286  lr: 0.0000
Epoch:[8/10] [48600/65469]  eta: 0:02:36  loss: 0.0826  step_time: 0.009210  lr: 0.0000
Epoch:[8/10] [48800/65469]  eta: 0:02:34  loss: 0.0697  step_time: 0.009250  lr: 0.0000
Epoch:[8/10] [49000/65469]  eta:

Test: [200/305]  loss: 0.0447  step_time: 0.0118
AUC computation took: 0.02 [s]
Epoch 8 step 65460. Test loss 0.04285, auc 0.939114
Saving a checkpoint to ./movie_lens_model
Checkpoint saving took 0.30 [s]
Epoch:[9/10] [200/65469]  eta: 0:10:06  loss: 0.0823  step_time: 0.031983  lr: 0.0000
Epoch:[9/10] [400/65469]  eta: 0:10:04  loss: 0.0717  step_time: 0.009198  lr: 0.0000
Epoch:[9/10] [600/65469]  eta: 0:10:02  loss: 0.0805  step_time: 0.009219  lr: 0.0000
Epoch:[9/10] [800/65469]  eta: 0:10:00  loss: 0.0762  step_time: 0.009201  lr: 0.0000
Epoch:[9/10] [1000/65469]  eta: 0:09:58  loss: 0.0721  step_time: 0.009202  lr: 0.0000
Epoch:[9/10] [1200/65469]  eta: 0:09:57  loss: 0.0697  step_time: 0.009200  lr: 0.0000
Epoch:[9/10] [1400/65469]  eta: 0:09:55  loss: 0.0783  step_time: 0.009197  lr: 0.0000
Epoch:[9/10] [1600/65469]  eta: 0:09:53  loss: 0.0742  step_time: 0.009216  lr: 0.0000
Epoch:[9/10] [1800/65469]  eta: 0:09:51  loss: 0.0779  step_time: 0.009204  lr: 0.0000
Epoch:[9/10] [2

Epoch:[9/10] [18600/65469]  eta: 0:07:15  loss: 0.0738  step_time: 0.009212  lr: 0.0000
Epoch:[9/10] [18800/65469]  eta: 0:07:13  loss: 0.0784  step_time: 0.009215  lr: 0.0000
Epoch:[9/10] [19000/65469]  eta: 0:07:11  loss: 0.0778  step_time: 0.009209  lr: 0.0000
Epoch:[9/10] [19200/65469]  eta: 0:07:09  loss: 0.0759  step_time: 0.009228  lr: 0.0000
Epoch:[9/10] [19400/65469]  eta: 0:07:07  loss: 0.0743  step_time: 0.009223  lr: 0.0000
Epoch:[9/10] [19600/65469]  eta: 0:07:06  loss: 0.0825  step_time: 0.009219  lr: 0.0000
Epoch:[9/10] [19800/65469]  eta: 0:07:04  loss: 0.0738  step_time: 0.009203  lr: 0.0000
Epoch:[9/10] [20000/65469]  eta: 0:07:02  loss: 0.0778  step_time: 0.009250  lr: 0.0000
Epoch:[9/10] [20200/65469]  eta: 0:07:00  loss: 0.0704  step_time: 0.009421  lr: 0.0000
Epoch:[9/10] [20400/65469]  eta: 0:06:58  loss: 0.0716  step_time: 0.009334  lr: 0.0000
Epoch:[9/10] [20600/65469]  eta: 0:06:56  loss: 0.0825  step_time: 0.009218  lr: 0.0000
Epoch:[9/10] [20800/65469]  eta:

Epoch:[9/10] [37400/65469]  eta: 0:04:20  loss: 0.0789  step_time: 0.009228  lr: 0.0000
Epoch:[9/10] [37600/65469]  eta: 0:04:18  loss: 0.0736  step_time: 0.009218  lr: 0.0000
Epoch:[9/10] [37800/65469]  eta: 0:04:16  loss: 0.0700  step_time: 0.009197  lr: 0.0000
Epoch:[9/10] [38000/65469]  eta: 0:04:15  loss: 0.0738  step_time: 0.009221  lr: 0.0000
Epoch:[9/10] [38200/65469]  eta: 0:04:13  loss: 0.0746  step_time: 0.009226  lr: 0.0000
Epoch:[9/10] [38400/65469]  eta: 0:04:11  loss: 0.0809  step_time: 0.009198  lr: 0.0000
Epoch:[9/10] [38600/65469]  eta: 0:04:09  loss: 0.0760  step_time: 0.009209  lr: 0.0000
Epoch:[9/10] [38800/65469]  eta: 0:04:07  loss: 0.0782  step_time: 0.009204  lr: 0.0000
Epoch:[9/10] [39000/65469]  eta: 0:04:05  loss: 0.0774  step_time: 0.009213  lr: 0.0000
Epoch:[9/10] [39200/65469]  eta: 0:04:03  loss: 0.0704  step_time: 0.009217  lr: 0.0000
Epoch:[9/10] [39400/65469]  eta: 0:04:02  loss: 0.0802  step_time: 0.009219  lr: 0.0000
Epoch:[9/10] [39600/65469]  eta:

Epoch:[9/10] [56200/65469]  eta: 0:01:26  loss: 0.0745  step_time: 0.009221  lr: 0.0000
Epoch:[9/10] [56400/65469]  eta: 0:01:24  loss: 0.0835  step_time: 0.009223  lr: 0.0000
Epoch:[9/10] [56600/65469]  eta: 0:01:22  loss: 0.0722  step_time: 0.009241  lr: 0.0000
Epoch:[9/10] [56800/65469]  eta: 0:01:20  loss: 0.0756  step_time: 0.009201  lr: 0.0000
Epoch:[9/10] [57000/65469]  eta: 0:01:18  loss: 0.0717  step_time: 0.009192  lr: 0.0000
Epoch:[9/10] [57200/65469]  eta: 0:01:16  loss: 0.0770  step_time: 0.009203  lr: 0.0000
Epoch:[9/10] [57400/65469]  eta: 0:01:14  loss: 0.0701  step_time: 0.009207  lr: 0.0000
Epoch:[9/10] [57600/65469]  eta: 0:01:13  loss: 0.0786  step_time: 0.009197  lr: 0.0000
Epoch:[9/10] [57800/65469]  eta: 0:01:11  loss: 0.0726  step_time: 0.009191  lr: 0.0000
Epoch:[9/10] [58000/65469]  eta: 0:01:09  loss: 0.0779  step_time: 0.009257  lr: 0.0000
Epoch:[9/10] [58200/65469]  eta: 0:01:07  loss: 0.0758  step_time: 0.009356  lr: 0.0000
Epoch:[9/10] [58400/65469]  eta: